In [275]:
import mysql.connector

In [276]:
import config

In [277]:
cnx = mysql.connector .connect(
    host = config.host,
    user = config.user,
    passwd = config.passwd
)

config.host

'flatiron.codm2dacov9z.us-east-2.rds.amazonaws.com'

In [278]:
cursor = cnx.cursor()

In [ ]:
cursor.execute("""
    CREATE USER 
        'finch'@'%' 
    IDENTIFIED BY 
        'Flatiron1000';
    GRANT ALL PRIVILEGES ON 
        * . * 
    TO 
        'finch'@'%';
    FLUSH PRIVILEGES;"""

cursor.fetchall()

In [283]:
from mysql.connector import errorcode

db_name = "microsoft"

def create_database(cursor, database):
    try:
        cursor.execute(
            "CREATE DATABASE {} DEFAULT CHARACTER SET 'utf8'".format(database))
    except mysql.connector.Error as err:
        print("Failed creating database: {}".format(err))
        exit(1)

try:
    cursor.execute("USE {}".format(db_name))
except mysql.connector.Error as err:
    print("Database {} does not exists.".format(db_name))
    if err.errno == errorcode.ER_BAD_DB_ERROR:
        create_database(cursor, db_name)
        print("Database {} created successfully.".format(db_name))
        cnx.database = db_name
    else:
        print(err)
        exit(1)

In [284]:
# Create a table for the IMDB data
DB_NAME = 'microsoft'

TABLES = {}
TABLES['imdb_movies'] = (
    "CREATE TABLE imdb_movies ("
    "  id varchar(255) NOT NULL UNIQUE PRIMARY KEY,"
    "  title varchar(255) NOT NULL,"
    "  year int NOT NULL,"
    "  runtime int NOT NULL,"
    "  genres varchar(255) NOT NULL,"
    "  rating float NOT NULL,"
    "  numVotes int NOT NULL"
    ") ENGINE=InnoDB")

TABLES['imdb_names'] = (
    "CREATE TABLE imdb_names ("
    "  person_id varchar(255) NOT NULL PRIMARY KEY,"
    "  name varchar(255) NOT NULL,"
    "  birthYear int NOT NULL,"
    "  profession varchar(255) NOT NULL,"
    "  imdb_id varchar(255) NOT NULL,"
    "  FOREIGN KEY (imdb_id) REFERENCES imdb_movies (imdb_id)"
    ") ENGINE=InnoDB")

In [285]:
from mysql.connector import errorcode

db_name = "microsoft"

for table_name in TABLES:
    table_description = TABLES[table_name]
    try:
        print("Creating table {}: ".format(table_name), end='')
        cursor.execute(table_description)
    except mysql.connector.Error as err:
        if err.errno == errorcode.ER_TABLE_EXISTS_ERROR:
            print("already exists.")
        else:
            print(err.msg)
    else:
        print("OK")

Creating table imdb_movies: OK
Creating table imdb_names: Failed to add the foreign key constraint. Missing column 'imdb_id' for constraint 'imdb_names_ibfk_1' in the referenced table 'imdb_movies'


In [315]:
movie_tuples = [tuple(x) for x in df_movies.values]

movie_tuples

[('tt0000574',
  'The Story of the Kelly Gang',
  1906,
  '70',
  'Biography,Crime,Drama',
  6.1,
  535.0),
 ('tt0001184',
  'Don Juan de Serrallonga',
  1910,
  '58',
  'Adventure,Drama',
  3.1,
  11.0),
 ('tt0001285',
  'The Life of Moses',
  1909,
  '50',
  'Biography,Drama,Family',
  5.1,
  30.0),
 ('tt0001790',
  'Les Misérables, Part 1: Jean Valjean',
  1913,
  '60',
  'Drama',
  5.8,
  21.0),
 ('tt0001812', 'Oedipus Rex', 1911, '56', 'Drama', 5.8, 6.0),
 ('tt0001892', 'Den sorte drøm', 1911, '53', 'Drama', 5.9, 169.0),
 ('tt0001911', 'Nell Gwynne', 1911, '50', 'Biography,Drama,History', 4.1, 7.0),
 ('tt0001964', 'The Traitress', 1911, '48', 'Drama', 6.1, 47.0),
 ('tt0002026',
  'Anny - Story of a Prostitute',
  1912,
  '68',
  'Drama,Romance',
  4.0,
  7.0),
 ('tt0002130',
  "Dante's Inferno",
  1911,
  '68',
  'Adventure,Drama,Fantasy',
  7.0,
  2005.0),
 ('tt0002186', 'The Flying Circus', 1912, '46', 'Drama', 6.4, 74.0),
 ('tt0002199',
  'From the Manger to the Cross; or, Jesu

In [316]:
def db_insert(list_of_tuples):
    insert_query = """INSERT INTO imdb_movies (id, title, year, runtime, genres, ratings, numVotes) 
                VALUES (%s, %s, %s, %s, %s, %s, %s);"""
    cursor.executemany(insert_query, list_of_tuples)
    cnx.commit()

In [317]:
db_insert(movie_tuples)

ProgrammingError: 1054 (42S22): Unknown column 'ratings' in 'field list'

In [270]:
name_tuples = [tuple(x) for x in df_name.values]

name_tuples

[('nm0000001',
  'Fred Astaire',
  '1899',
  '1987',
  'soundtrack,actor,miscellaneous',
  'tt0072308,tt0043044,tt0050419,tt0053137'),
 ('nm0000002',
  'Lauren Bacall',
  '1924',
  '2014',
  'actress,soundtrack',
  'tt0038355,tt0117057,tt0037382,tt0071877'),
 ('nm0000003',
  'Brigitte Bardot',
  '1934',
  nan,
  'actress,soundtrack,producer',
  'tt0057345,tt0054452,tt0049189,tt0059956'),
 ('nm0000004',
  'John Belushi',
  '1949',
  '1982',
  'actor,writer,soundtrack',
  'tt0078723,tt0077975,tt0072562,tt0080455'),
 ('nm0000005',
  'Ingmar Bergman',
  '1918',
  '2007',
  'writer,director,actor',
  'tt0050986,tt0050976,tt0083922,tt0069467'),
 ('nm0000006',
  'Ingrid Bergman',
  '1915',
  '1982',
  'actress,soundtrack,producer',
  'tt0036855,tt0038109,tt0038787,tt0071877'),
 ('nm0000007',
  'Humphrey Bogart',
  '1899',
  '1957',
  'actor,soundtrack,producer',
  'tt0043265,tt0037382,tt0034583,tt0033870'),
 ('nm0000008',
  'Marlon Brando',
  '1924',
  '2004',
  'actor,soundtrack,director',
 

## 1. IMDB Database

In [112]:
import pandas as pd

In [3]:
df_name = pd.read_table('name.basics.tsv.gz')

In [4]:
df_name.head(20)

nconst          primaryName birthYear deathYear  \
0   nm0000001         Fred Astaire      1899      1987   
1   nm0000002        Lauren Bacall      1924      2014   
2   nm0000003      Brigitte Bardot      1934        \N   
3   nm0000004         John Belushi      1949      1982   
4   nm0000005       Ingmar Bergman      1918      2007   
5   nm0000006       Ingrid Bergman      1915      1982   
6   nm0000007      Humphrey Bogart      1899      1957   
7   nm0000008        Marlon Brando      1924      2004   
8   nm0000009       Richard Burton      1925      1984   
9   nm0000010         James Cagney      1899      1986   
10  nm0000011          Gary Cooper      1901      1961   
11  nm0000012          Bette Davis      1908      1989   
12  nm0000013            Doris Day      1922      2019   
13  nm0000014  Olivia de Havilland      1916        \N   
14  nm0000015           James Dean      1931      1955   
15  nm0000016      Georges Delerue      1925      1992   
16  nm0000017     Marlene Dietrich      1901      1992   
17  nm0000018         Kirk Douglas      1916        \N   
18  nm0000019     Federico Fellini      1920      1993   
19  nm0000020          Henry Fonda      1905      1982   

                        primaryProfession  \
0          soundtrack,actor,miscellaneous   
1                      actress,soundtrack   
2             actress,soundtrack,producer   
3                 actor,writer,soundtrack   
4                   writer,director,actor   
5             actress,soundtrack,producer   
6               actor,soundtrack,producer   
7               actor,soundtrack,director   
8               actor,producer,soundtrack   
9               actor,soundtrack,director   
10              actor,soundtrack,producer   
11  actress,soundtrack,make_up_department   
12            soundtrack,actress,producer   
13                     actress,soundtrack   
14                    actor,miscellaneous   
15   composer,soundtrack,music_department   
16    soundtrack,actress,music_department   
17              actor,producer,soundtrack   
18     writer,director,assistant_director   
19              actor,producer,soundtrack   

                             knownForTitles  
0   tt0072308,tt0043044,tt0050419,tt0053137  
1   tt0038355,tt0117057,tt0037382,tt0071877  
2   tt0057345,tt0054452,tt0049189,tt0059956  
3   tt0078723,tt0077975,tt0072562,tt0080455  
4   tt0050986,tt0050976,tt0083922,tt0069467  
5   tt0036855,tt0038109,tt0038787,tt0071877  
6   tt0043265,tt0037382,tt0034583,tt0033870  
7   tt0068646,tt0047296,tt0078788,tt0070849  
8   tt0087803,tt0059749,tt0057877,tt0061184  
9   tt0035575,tt0031867,tt0029870,tt0042041  
10  tt0034167,tt0035896,tt0044706,tt0027996  
11  tt0042192,tt0031210,tt0056687,tt0035140  
12  tt0048317,tt0055100,tt0053172,tt0060463  
13  tt0031381,tt0029843,tt0041452,tt0040806  
14  tt0049261,tt0039123,tt0048028,tt0048545  
15  tt0091763,tt0096320,tt0069946,tt0057345  
16  tt0051201,tt0052311,tt0055031,tt0021156  
17  tt0049456,tt0054331,tt0052365,tt0080736  
18  tt0056801,tt0071129,tt0047528,tt0053779  
19  tt0032551,tt0082846,tt0064116,tt0050083

In [219]:
na_dict = {'\\N': np.nan}
df_name['deathYear'] = df_name['deathYear'].replace(na_dict)

In [220]:
df_name.head()

nconst      primaryName birthYear deathYear  \
0  nm0000001     Fred Astaire      1899      1987   
1  nm0000002    Lauren Bacall      1924      2014   
2  nm0000003  Brigitte Bardot      1934       NaN   
3  nm0000004     John Belushi      1949      1982   
4  nm0000005   Ingmar Bergman      1918      2007   

                primaryProfession                           knownForTitles  
0  soundtrack,actor,miscellaneous  tt0072308,tt0043044,tt0050419,tt0053137  
1              actress,soundtrack  tt0038355,tt0117057,tt0037382,tt0071877  
2     actress,soundtrack,producer  tt0057345,tt0054452,tt0049189,tt0059956  
3         actor,writer,soundtrack  tt0078723,tt0077975,tt0072562,tt0080455  
4           writer,director,actor  tt0050986,tt0050976,tt0083922,tt0069467

In [293]:
df_title = pd.read_table('title.basics.tsv.gz')

/Users/michaeleby1/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3058: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [294]:
df_title.head(20)

tconst titleType                                 primaryTitle  \
0   tt0000001     short                                   Carmencita   
1   tt0000002     short                       Le clown et ses chiens   
2   tt0000003     short                               Pauvre Pierrot   
3   tt0000004     short                                  Un bon bock   
4   tt0000005     short                             Blacksmith Scene   
5   tt0000006     short                            Chinese Opium Den   
6   tt0000007     short  Corbett and Courtney Before the Kinetograph   
7   tt0000008     short       Edison Kinetoscopic Record of a Sneeze   
8   tt0000009     movie                                   Miss Jerry   
9   tt0000010     short                          Exiting the Factory   
10  tt0000011     short                      Akrobatisches Potpourri   
11  tt0000012     short                       The Arrival of a Train   
12  tt0000013     short  The Photographical Congress Arrives in Lyon   
13  tt0000014     short                      The Sprinkler Sprinkled   
14  tt0000015     short                          Autour d'une cabine   
15  tt0000016     short                       Barque sortant du port   
16  tt0000017     short                     Italienischer Bauerntanz   
17  tt0000018     short                         Das boxende Känguruh   
18  tt0000019     short                             The Clown Barber   
19  tt0000020     short                               The Derby 1895   

                                        originalTitle  isAdult startYear  \
0                                          Carmencita        0      1894   
1                              Le clown et ses chiens        0      1892   
2                                      Pauvre Pierrot        0      1892   
3                                         Un bon bock        0      1892   
4                                    Blacksmith Scene        0      1893   
5                                   Chinese Opium Den        0      1894   
6         Corbett and Courtney Before the Kinetograph        0      1894   
7              Edison Kinetoscopic Record of a Sneeze        0      1894   
8                                          Miss Jerry        0      1894   
9                 La sortie de l'usine Lumière à Lyon        0      1895   
10                            Akrobatisches Potpourri        0      1895   
11                   L'arrivée d'un train à La Ciotat        0      1896   
12  Neuville-sur-Saône: Débarquement du congrès de...        0      1895   
13                                  L'arroseur arrosé        0      1895   
14                                Autour d'une cabine        0      1894   
15                             Barque sortant du port        0      1895   
16                           Italienischer Bauerntanz        0      1895   
17                               Das boxende Känguruh        0      1895   
18                                   The Clown Barber        0      1898   
19                                     The Derby 1895        0      1895   

   endYear runtimeMinutes                    genres  
0       \N              1         Documentary,Short  
1       \N              5           Animation,Short  
2       \N              4  Animation,Comedy,Romance  
3       \N             \N           Animation,Short  
4       \N              1              Comedy,Short  
5       \N              1                     Short  
6       \N              1               Short,Sport  
7       \N              1         Documentary,Short  
8       \N             45                   Romance  
9       \N              1         Documentary,Short  
10      \N              1         Documentary,Short  
11      \N              1  Action,Documentary,Short  
12      \N              1         Documentary,Short  
13      \N              1              Comedy,Short  
14      \N              2           Animation,Short  
15      \N              1        

In [295]:
df_title[df_title['tconst'] == 'tt0068646'] 

tconst titleType   primaryTitle  originalTitle  isAdult startYear  \
67299  tt0068646     movie  The Godfather  The Godfather        0      1972   

      endYear runtimeMinutes       genres  
67299      \N            175  Crime,Drama

In [296]:
df_ratings = pd.read_table('title.ratings.tsv.gz')

In [297]:
df_ratings.head(20)

tconst  averageRating  numVotes
0   tt0000001            5.6      1545
1   tt0000002            6.1       187
2   tt0000003            6.5      1202
3   tt0000004            6.2       114
4   tt0000005            6.1      1924
5   tt0000006            5.2       102
6   tt0000007            5.4       612
7   tt0000008            5.4      1654
8   tt0000009            5.4        81
9   tt0000010            6.9      5518
10  tt0000011            5.2       235
11  tt0000012            7.4      9390
12  tt0000013            5.7      1438
13  tt0000014            7.1      4096
14  tt0000015            6.1       737
15  tt0000016            5.9      1077
16  tt0000017            4.7       214
17  tt0000018            5.4       445
18  tt0000019            5.6        16
19  tt0000020            5.0       248

In [298]:
df_ratings.set_index('tconst')

averageRating  numVotes
tconst                            
tt0000001            5.6      1545
tt0000002            6.1       187
tt0000003            6.5      1202
tt0000004            6.2       114
tt0000005            6.1      1924
...                  ...       ...
tt9916576            5.9         7
tt9916578            9.1        11
tt9916720            5.1        41
tt9916766            6.7        11
tt9916778            6.9        16

[986685 rows x 2 columns]

In [299]:
df_ratings[df_ratings['numVotes'] >= 250000] # Use the number of votes as a measure of a film's success

tconst  averageRating  numVotes
13726   tt0031381            8.1    269068
14328   tt0032138            8.0    356917
15398   tt0033467            8.3    370950
16320   tt0034583            8.5    486509
19570   tt0038650            8.6    365546
...           ...            ...       ...
837374  tt5580390            7.3    324768
889384  tt6644200            7.5    329961
902913  tt6966692            8.2    254325
915887  tt7286456            8.8    399043
918664  tt7366338            9.5    375977

[634 rows x 3 columns]

In [300]:
df_ratings[df_ratings['tconst'] == 'tt0068646'] #The Godfather 

tconst  averageRating  numVotes
44697  tt0068646            9.2   1477555

In [301]:
df_ratings.shape

(986685, 3)

In [302]:
df_movies = df_title[df_title['titleType'] == 'movie']
df_movies.head()

tconst titleType                   primaryTitle  \
8    tt0000009     movie                     Miss Jerry   
145  tt0000147     movie  The Corbett-Fitzsimmons Fight   
332  tt0000335     movie          Soldiers of the Cross   
499  tt0000502     movie                       Bohemios   
571  tt0000574     movie    The Story of the Kelly Gang   

                     originalTitle  isAdult startYear endYear runtimeMinutes  \
8                       Miss Jerry        0      1894      \N             45   
145  The Corbett-Fitzsimmons Fight        0      1897      \N             20   
332          Soldiers of the Cross        0      1900      \N             \N   
499                       Bohemios        0      1905      \N            100   
571    The Story of the Kelly Gang        0      1906      \N             70   

                     genres  
8                   Romance  
145  Documentary,News,Sport  
332         Biography,Drama  
499                      \N  
571   Biography,Crime,Drama

In [303]:
df_movies.drop(['titleType', 'originalTitle', 'isAdult', 'endYear'], axis=1, inplace=True)
df_movies.shape

(534215, 5)

In [304]:
df_movies = df_movies[df_movies['runtimeMinutes'] > '45']

import numpy as np

na_dict = {'\\N': np.nan}
df_movies['runtimeMinutes'] = df_movies['runtimeMinutes'].replace(na_dict)
df_movies['startYear'] = df_movies['startYear'].replace(na_dict)
df_movies['genres'] = df_movies['genres'].replace(na_dict)

df_movies = df_movies.rename(columns={'startYear': 'year', 'runtimeMinutes': 'runtime', 'primaryTitle': 'title'})



In [305]:
df_movies = df_movies.dropna()
df_movies.head()

tconst                                 title  year runtime  \
571   tt0000574           The Story of the Kelly Gang  1906      70   
1173  tt0001184               Don Juan de Serrallonga  1910      58   
1274  tt0001285                     The Life of Moses  1909      50   
1486  tt0001498               The Battle of Trafalgar  1911      51   
1774  tt0001790  Les Misérables, Part 1: Jean Valjean  1913      60   

                      genres  
571    Biography,Crime,Drama  
1173         Adventure,Drama  
1274  Biography,Drama,Family  
1486                     War  
1774                   Drama

In [306]:
df_movies.set_index('tconst')

title  year runtime  \
tconst                                                                       
tt0000574                        The Story of the Kelly Gang  1906      70   
tt0001184                            Don Juan de Serrallonga  1910      58   
tt0001285                                  The Life of Moses  1909      50   
tt0001498                            The Battle of Trafalgar  1911      51   
tt0001790               Les Misérables, Part 1: Jean Valjean  1913      60   
...                                                      ...   ...     ...   
tt9916132                       The Mystery of a Buryat Lama  2018      94   
tt9916160                                         Drømmeland  2019      72   
tt9916170                                      The Rehearsal  2019      51   
tt9916186  Illenau - die Geschichte einer ehemaligen Heil...  2017      84   
tt9916190                                          Safeguard  2020      90   

                                  genres  
tconst                                    
tt0000574          Biography,Crime,Drama  
tt0001184                Adventure,Drama  
tt0001285         Biography,Drama,Family  
tt0001498                            War  
tt0001790                          Drama  
...                                  ...  
tt9916132  Biography,Documentary,History  
tt9916160                    Documentary  
tt9916170                          Drama  
tt9916186                    Documentary  
tt9916190                Action,Thriller  

[219350 rows x 4 columns]

In [307]:
# pd.concat([df_movies, df_ratings], names='tconst', join='outer', axis=1)

df_movies = df_movies.set_index('tconst').join(df_ratings.set_index('tconst'))
df_movies.head()


title  year runtime  \
tconst                                                          
tt0000574           The Story of the Kelly Gang  1906      70   
tt0001184               Don Juan de Serrallonga  1910      58   
tt0001285                     The Life of Moses  1909      50   
tt0001498               The Battle of Trafalgar  1911      51   
tt0001790  Les Misérables, Part 1: Jean Valjean  1913      60   

                           genres  averageRating  numVotes  
tconst                                                      
tt0000574   Biography,Crime,Drama            6.1     535.0  
tt0001184         Adventure,Drama            3.1      11.0  
tt0001285  Biography,Drama,Family            5.1      30.0  
tt0001498                     War            NaN       NaN  
tt0001790                   Drama            5.8      21.0

In [308]:
df_movies = df_movies.dropna()
df_movies.head()


title  year runtime  \
tconst                                                          
tt0000574           The Story of the Kelly Gang  1906      70   
tt0001184               Don Juan de Serrallonga  1910      58   
tt0001285                     The Life of Moses  1909      50   
tt0001790  Les Misérables, Part 1: Jean Valjean  1913      60   
tt0001812                           Oedipus Rex  1911      56   

                           genres  averageRating  numVotes  
tconst                                                      
tt0000574   Biography,Crime,Drama            6.1     535.0  
tt0001184         Adventure,Drama            3.1      11.0  
tt0001285  Biography,Drama,Family            5.1      30.0  
tt0001790                   Drama            5.8      21.0  
tt0001812                   Drama            5.8       6.0

In [312]:
df_movies = df_movies.reset_index()

In [313]:
df_movies

tconst                                 title  year runtime  \
0       tt0000574           The Story of the Kelly Gang  1906      70   
1       tt0001184               Don Juan de Serrallonga  1910      58   
2       tt0001285                     The Life of Moses  1909      50   
3       tt0001790  Les Misérables, Part 1: Jean Valjean  1913      60   
4       tt0001812                           Oedipus Rex  1911      56   
...           ...                                   ...   ...     ...   
141496  tt9910930                           Jeg ser deg  2019      75   
141497  tt9913056                          Swarm Season  2019      86   
141498  tt9913084                      Diabolik sono io  2019      75   
141499  tt9914286                     Sokagin Çocuklari  2019      98   
141500  tt9916160                            Drømmeland  2019      72   

                        genres  averageRating  numVotes  
0        Biography,Crime,Drama            6.1     535.0  
1              Adventure,Drama            3.1      11.0  
2       Biography,Drama,Family            5.1      30.0  
3                        Drama            5.8      21.0  
4                        Drama            5.8       6.0  
...                        ...            ...       ...  
141496       Crime,Documentary            6.1       7.0  
141497             Documentary            6.9       7.0  
141498             Documentary            6.2       6.0  
141499            Drama,Family            7.2     190.0  
141500             Documentary            6.5      31.0  

[141501 rows x 7 columns]

## 2. The Movie Database API

In [12]:
import json
import requests

api_key = '4f3f2d2aea79f403399bd52376f7aa1d' 

In [13]:
def themoviedb_call(api_key, imdb_id):
    url = f'https://api.themoviedb.org/3/find/{imdb_id}?api_key={api_key}&language=en-US&external_source=imdb_id'
    response = requests.get(url)
    data = response.json()['movie_results'][0]
    data['imdb_id'] = imdb_id
    return data

In [191]:
themoviedb_call(api_key, 'tt0068646')

{'id': 238,
 'video': False,
 'vote_count': 10799,
 'vote_average': 8.6,
 'title': 'The Godfather',
 'release_date': '1972-03-14',
 'original_language': 'en',
 'original_title': 'The Godfather',
 'genre_ids': [80, 18],
 'backdrop_path': '/6xKCYgH16UuwEGAyroLU6p8HLIn.jpg',
 'adult': False,
 'overview': 'Spanning the years 1945 to 1955, a chronicle of the fictional Italian-American Corleone crime family. When organized crime family patriarch, Vito Corleone barely survives an attempt on his life, his youngest son, Michael steps in to take care of the would-be killers, launching a campaign of bloody revenge.',
 'poster_path': '/rPdtLWNsZmAtoZl9PK7S2wE3qiS.jpg',
 'popularity': 31.278,
 'imdb_id': 'tt0068646'}

In [ ]:
# write a function that loops through themoviedb_call with imdb_ids 

## 3. Web-Scraping: Press for Films Currently Streaming

In [20]:
page = requests.get('https://web.archive.org/web/20190527114817/https://www.vulture.com/article/best-movies-amazon-prime.html')
page.status_code

200

In [21]:
page.content

b'  <!DOCTYPE html>\n<html lang="en" data-uri="www.vulture.com/_pages/cjtt84iyj003ma2y628qamili@published" data-layout-uri="www.vulture.com/_layouts/layout/instances/article@published">\n  <head><script src="//archive.org/includes/analytics.js?v=cf34f82" type="text/javascript"></script>\n<script type="text/javascript">window.addEventListener(\'DOMContentLoaded\',function(){var v=archive_analytics.values;v.service=\'wb\';v.server_name=\'wwwb-app103.us.archive.org\';v.server_ms=431;archive_analytics.send_pageview({});});</script><script type="text/javascript" src="/_static/js/ait-client-rewrite.js" charset="utf-8"></script>\n<script type="text/javascript">\nWB_wombat_Init("https://web.archive.org/web/", "20190527114817", "www.vulture.com");\n</script>\n<script type="text/javascript" src="/_static/js/wbhack.js" charset="utf-8"></script>\n<script type="text/javascript">\n__wbhack.init(\'https://web.archive.org/web\');\n</script>\n<link rel="stylesheet" type="text/css" href="/_static/css/ba

In [115]:
from bs4 import BeautifulSoup
vulture_may = BeautifulSoup(page.content, 'html.parser')
vulture_may

 <!DOCTYPE html>

<html data-layout-uri="www.vulture.com/_layouts/layout/instances/article@published" data-uri="www.vulture.com/_pages/cjtt84iyj003ma2y628qamili@published" lang="en">
<head><script src="//archive.org/includes/analytics.js?v=cf34f82" type="text/javascript"></script>
<script type="text/javascript">window.addEventListener('DOMContentLoaded',function(){var v=archive_analytics.values;v.service='wb';v.server_name='wwwb-app103.us.archive.org';v.server_ms=431;archive_analytics.send_pageview({});});</script><script charset="utf-8" src="/_static/js/ait-client-rewrite.js" type="text/javascript"></script>
<script type="text/javascript">
WB_wombat_Init("https://web.archive.org/web/", "20190527114817", "www.vulture.com");
</script>
<script charset="utf-8" src="/_static/js/wbhack.js" type="text/javascript"></script>
<script type="text/javascript">
__wbhack.init('https://web.archive.org/web');
</script>
<link href="/_static/css/banner-styles.css" rel="stylesheet" type="text/css"/>
<lin

In [116]:
print(vulture_may.prettify())

<!DOCTYPE html>
<html data-layout-uri="www.vulture.com/_layouts/layout/instances/article@published" data-uri="www.vulture.com/_pages/cjtt84iyj003ma2y628qamili@published" lang="en">
 <head>
  <script src="//archive.org/includes/analytics.js?v=cf34f82" type="text/javascript">
  </script>
  <script type="text/javascript">
   window.addEventListener('DOMContentLoaded',function(){var v=archive_analytics.values;v.service='wb';v.server_name='wwwb-app103.us.archive.org';v.server_ms=431;archive_analytics.send_pageview({});});
  </script>
  <script charset="utf-8" src="/_static/js/ait-client-rewrite.js" type="text/javascript">
  </script>
  <script type="text/javascript">
   WB_wombat_Init("https://web.archive.org/web/", "20190527114817", "www.vulture.com");
  </script>
  <script charset="utf-8" src="/_static/js/wbhack.js" type="text/javascript">
  </script>
  <script type="text/javascript">
   __wbhack.init('https://web.archive.org/web');
  </script>
  <link href="/_static/css/banner-styles.css

In [117]:
strong = vulture_may.find_all('strong')
strong

[<strong><em>12 Angry Men</em></strong>,
 <strong><em>*The 39 Steps</em></strong>,
 <strong>*<em>A.I.: Artificial Intelligence</em></strong>,
 <strong><em>The Accused</em></strong>,
 <strong><em>The Act of Killing</em></strong>,
 <strong><em>Annihilation</em></strong>,
 <strong><em>The Apartment</em></strong>,
 <strong>*<em>Big Night</em></strong>,
 <strong><em>The Big Sick</em></strong>,
 <strong><em>Blue</em> <em>Velvet</em></strong>,
 <strong><em>The Blues Brothers</em></strong>,
 <strong><em>*Bone Tomahawk</em></strong>,
 <strong><em>Charade</em></strong>,
 <strong><em>Child’s Play</em></strong>,
 <strong><em>*Chinatown</em></strong>,
 <strong><em>*Cloverfield</em></strong>,
 <strong><em>Coherence</em></strong>,
 <strong><em>Cold War</em></strong>,
 <strong><em>The Conversation</em></strong>,
 <strong><em>Dead Ringers</em></strong>,
 <strong><em>The Dead Zone</em></strong>,
 <strong><em>Dear Zachary: A Letter to a Son About His Father</em></strong>,
 <strong><em>Deep Red</em></stro

In [119]:
titles = []
for i in list(range(len(strong))):
    titles.append(strong[i].get_text())
titles

['12 Angry Men',
 '*The 39 Steps',
 '*A.I.: Artificial Intelligence',
 'The Accused',
 'The Act of Killing',
 'Annihilation',
 'The Apartment',
 '*Big Night',
 'The Big Sick',
 'Blue Velvet',
 'The Blues Brothers',
 '*Bone Tomahawk',
 'Charade',
 'Child’s Play',
 '*Chinatown',
 '*Cloverfield',
 'Coherence',
 'Cold War',
 'The Conversation',
 'Dead Ringers',
 'The Dead Zone',
 'Dear Zachary: A Letter to a Son About His Father',
 'Deep Red',
 'Diabolique',
 '*The Disaster Artist',
 'Dressed to Kill',
 'Eighth Grade',
 '*Fargo',
 'First Reformed',
 'A Fistful of Dollars',
 'Fitzcarraldo',
 'The Florida Project',
 'Gangs of New York',
 'A Ghost Story',
 'Good Time',
 'The Handmaiden',
 'Heathers',
 'Henry: Portrait of a Serial Killer',
 'Hereditary',
 'High Noon',
 '*His Girl Friday',
 'Hoop Dreams',
 'Hotel Rwanda',
 'House of Games',
 'Hugo',
 'Hustle & Flow',
 'Inside Llewyn Davis',
 'Interview With the Vampire',
 'Invasion of the Body Snatchers',
 'It’s a Wonderful Life',
 'Joe',
 '*Th

In [93]:
page2 = requests.get('https://web.archive.org/web/20190330083826/https://www.vulture.com/article/best-movies-amazon-prime.html')
page2.status_code

200

In [97]:
vulture_march = BeautifulSoup(page2.content, 'html.parser')
print(vulture_march.prettify())

<!DOCTYPE html>
<html data-layout-uri="www.vulture.com/_layouts/layout/instances/article@published" data-uri="www.vulture.com/_pages/cjtt84iyj003ma2y628qamili@published" lang="en">
 <head>
  <script src="//archive.org/includes/analytics.js?v=cf34f82" type="text/javascript">
  </script>
  <script type="text/javascript">
   window.addEventListener('DOMContentLoaded',function(){var v=archive_analytics.values;v.service='wb';v.server_name='wwwb-app100.us.archive.org';v.server_ms=311;archive_analytics.send_pageview({});});
  </script>
  <script charset="utf-8" src="/_static/js/ait-client-rewrite.js" type="text/javascript">
  </script>
  <script type="text/javascript">
   WB_wombat_Init("https://web.archive.org/web/", "20190330083826", "www.vulture.com");
  </script>
  <script charset="utf-8" src="/_static/js/wbhack.js" type="text/javascript">
  </script>
  <script type="text/javascript">
   __wbhack.init('https://web.archive.org/web');
  </script>
  <link href="/_static/css/banner-styles.css

In [99]:
strong2 = vulture_march.find_all('strong')
strong2

[<strong><em>12 Angry Men</em></strong>,
 <strong><em>The Act of Killing</em></strong>,
 <strong><em>American Honey</em></strong>,
 <strong><em>Annihilation</em></strong>,
 <strong><em>The Apartment</em></strong>,
 <strong><em>Arrival</em></strong>,
 <strong><em>The Big Sick</em></strong>,
 <strong><em>Bill &amp; Ted’s Excellent Adventure</em></strong>,
 <strong><em>The Birdcage</em></strong>,
 <strong><em>The Blackcoat’s Daughter</em></strong>,
 <strong><em>Blue</em> <em>Velvet</em></strong>,
 <strong><em>The Blues Brothers</em></strong>,
 <strong><em>Bound</em></strong>,
 <strong><em>Brazil</em></strong>,
 <strong><em>Capote</em></strong>,
 <strong><em>Charade</em></strong>,
 <strong><em>Child’s Play</em></strong>,
 <strong><em>Chinatown</em></strong>,
 <strong><em>Coherence</em></strong>,
 <strong><em>Cold War</em></strong>,
 <strong><em>The Conversation</em></strong>,
 <strong><em>Dead Ringers</em></strong>,
 <strong><em>Dear Zachary: A Letter to a Son About His Father</em></strong

In [100]:
for i in list(range(len(strong2))):
    titles.append(strong2[i].get_text())
titles

['12 Angry Men',
 '*The 39 Steps',
 '*A.I.: Artificial Intelligence',
 'The Accused',
 'The Act of Killing',
 'Annihilation',
 'The Apartment',
 '*Big Night',
 'The Big Sick',
 'Blue Velvet',
 'The Blues Brothers',
 '*Bone Tomahawk',
 'Charade',
 'Child’s Play',
 '*Chinatown',
 '*Cloverfield',
 'Coherence',
 'Cold War',
 'The Conversation',
 'Dead Ringers',
 'The Dead Zone',
 'Dear Zachary: A Letter to a Son About His Father',
 'Deep Red',
 'Diabolique',
 '*The Disaster Artist',
 'Dressed to Kill',
 'Eighth Grade',
 '*Fargo',
 'First Reformed',
 'A Fistful of Dollars',
 'Fitzcarraldo',
 'The Florida Project',
 'Gangs of New York',
 'A Ghost Story',
 'Good Time',
 'The Handmaiden',
 'Heathers',
 'Henry: Portrait of a Serial Killer',
 'Hereditary',
 'High Noon',
 '*His Girl Friday',
 'Hoop Dreams',
 'Hotel Rwanda',
 'House of Games',
 'Hugo',
 'Hustle & Flow',
 'Inside Llewyn Davis',
 'Interview With the Vampire',
 'Invasion of the Body Snatchers',
 'It’s a Wonderful Life',
 'Joe',
 '*Th

In [109]:
titles = set(titles)
titles = list(titles)

In [111]:
type(titles)
titles

['American Honey',
 'Fitzcarraldo',
 'Transsiberian',
 '*A Quiet Place',
 'Wayne’s World',
 'Child’s Play',
 '*The Disaster Artist',
 'The Dead Zone',
 'Charade',
 '*A.I.: Artificial Intelligence',
 'The Apartment',
 'The Manchurian Candidate',
 'Midnight Cowboy',
 'Thunder Road',
 'Interview With the Vampire',
 'Lady Bird',
 'Platoon',
 'House of Games',
 'Chinatown',
 'In the Heat of the Night',
 'Get Shorty',
 'Dead Ringers',
 'The Big Sick',
 'Good Time',
 'Marathon Man',
 'Diabolique',
 'The Purple Rose of Cairo',
 'The Running Man',
 'Mud',
 'Zodiac',
 'Sophie’s Choice',
 'The Florida Project',
 'Lean on Pete',
 'Arrival',
 'The Lost City of Z',
 'Some Like It Hot',
 'Annihilation',
 'Memories of Murder',
 'It’s a Wonderful Life',
 'The Blackcoat’s Daughter',
 '12 Angry Men',
 'Hustle & Flow',
 'The Machinist',
 'Whale Rider',
 '*Murder on the Orient Express',
 '*The King of Comedy',
 'Bill & Ted’s Excellent Adventure',
 'The Messenger',
 '*A Simple Plan',
 'Capote',
 'Mother!',


In [113]:
len(titles)

131

In [139]:
paste_magazine = requests.get('https://www.pastemagazine.com/articles/2019/10/best-movies-on-netflix.html')
paste_magazine.status_code

200

In [140]:
paste_magazine = BeautifulSoup(paste_magazine.content, 'html.parser')


In [141]:
print(paste_magazine.prettify())

<!DOCTYPE doctype html>
<html class="no-js" dir="ltr" lang="en">
 <head id="Meta_HeadTag">
  <title>
   Paste Magazine - The Best Music, Movies and More
  </title>
  <meta charset="utf-8"/>
  <link href="/pastemagazine.img/favicon.ico" rel="shortcut icon" type="image/vnd.microsoft.icon"/>
  <script>
   var pm = {
   servers: {
       pastemagazine: "www.pastemagazine.com",
       wolfgangs: "www.wolfgangs.com"
   },
   version: "39.2019.11025.11957.2",
   page: {"type":"Landing","mediaType":"Unknown","articleType":"Unknown","articleId":-1,"author":null,"services":"/pastemagazine.svc/pastemagazine/","isMobile":false,"isIos":false,"videoEmbedPlayerId":30540132,"testGroup":"true"}
};
  </script>
  <!-- Google Tag Manager -->
  <script id="gtm-script">
   (function(w,d,s,l,i){w[l]=w[l]||[];w[l].push({'gtm.start':
new Date().getTime(),event:'gtm.js'});var f=d.getElementsByTagName(s)[0],
j=d.createElement(s),dl=l!='dataLayer'?'&l='+l:'';j.async=true;j.src=
'//www.googletagmanager.com/gtm.js?

In [160]:
containers = paste_magazine.find_all(class_="grid-container")

In [161]:
containers.find_all("ovr")

AttributeError: ResultSet object has no attribute 'find_all'. You're probably treating a list of items like a single item. Did you call find_all() when you meant to call find()?

In [162]:
afi_top_100 = requests.get("https://www.afi.com/afis-100-years-100-movies-10th-anniversary-edition/")
afi_top_100.status_code

200

In [163]:
afi_top_100 = BeautifulSoup(afi_top_100.content, 'html.parser')
afi_top_100

<!DOCTYPE html>

<html lang="en">
<head>
<title>AFI’S 100 YEARS…100 MOVIES — 10TH ANNIVERSARY EDITION | American Film Institute</title>
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<link href="https://devaficalmjediwestussa.blob.core.windows.net/images/2019/09/favicon.ico" rel="icon" type="image/png"/>
<!-- Global site tag (gtag.js) - Google Analytics -->
<script async="" src="https://www.googletagmanager.com/gtag/js?id=UA-9824359-2"></script>
<script>
  window.dataLayer = window.dataLayer || [];
  function gtag(){dataLayer.push(arguments);}
  gtag('js', new Date());

  gtag('config', 'UA-9824359-2');
</script> <title>AFI’S 100 YEARS…100 MOVIES — 10TH ANNIVERSARY EDITION – American Film Institute</title>
<script type="text/javascript">function heateorSssLoadEvent(e) {var t=window.onload;if (typeof window.onload!="function") {window.onload=e}else{window.onload=function() {t();e()}}};	var heateorSssSharingAjaxUrl = 'https://www.afi.com/w

In [164]:
afi_top_100 = afi_top_100.find_all(class_='q_title')

In [166]:
def find_titles(data):
    all_titles = []
    for i in range(len(data)):
        all_titles.append(data[i].get_text())
    return all_titles

afi_100 = find_titles(afi_top_100)
afi_100

['1. CITIZEN KANE (1941)',
 '2. THE GODFATHER (1972)',
 '3. CASABLANCA (1943)',
 '4. RAGING BULL (1980)',
 "5. SINGIN' IN THE RAIN (1952)",
 '6. GONE WITH THE WIND (1940)',
 '7. LAWRENCE OF ARABIA (1962)',
 "8. SCHINDLER'S LIST (1993)",
 '9. VERTIGO (1958)',
 '10. THE WIZARD OF OZ (1939)',
 '11. CITY LIGHTS (1931)',
 '12. THE SEARCHERS (1956)',
 '13. STAR WARS (1977)',
 '14. PSYCHO (1960)',
 '15. 2001: A SPACE ODYSSEY (1968)',
 '16. SUNSET BLVD. (1950)',
 '17. THE GRADUATE (1967)',
 '18. THE GENERAL (1927)',
 '19. ON THE WATERFRONT (1954)',
 "20. IT'S A WONDERFUL LIFE (1947)",
 '21. CHINATOWN (1974)',
 '22. SOME LIKE IT HOT (1959)',
 '23. THE GRAPES OF WRATH (1940)',
 '24. E.T.:  THE EXTRA-TERRESTRIAL (1982)',
 '25. TO KILL A MOCKINGBIRD (1962)',
 '26. MR. SMITH GOES TO WASHINGTON (1939)',
 '27. HIGH NOON (1952)',
 '28. ALL ABOUT EVE (1950)',
 '29. DOUBLE INDEMNITY (1944)',
 '30. APOCALYPSE NOW (1979)',
 '31. THE MALTESE FALCON (1941)',
 '32. THE GODFATHER PART II (1974)',
 "33. ONE FL

In [167]:
afi_100 = afi_100[:100]
afi_100

['1. CITIZEN KANE (1941)',
 '2. THE GODFATHER (1972)',
 '3. CASABLANCA (1943)',
 '4. RAGING BULL (1980)',
 "5. SINGIN' IN THE RAIN (1952)",
 '6. GONE WITH THE WIND (1940)',
 '7. LAWRENCE OF ARABIA (1962)',
 "8. SCHINDLER'S LIST (1993)",
 '9. VERTIGO (1958)',
 '10. THE WIZARD OF OZ (1939)',
 '11. CITY LIGHTS (1931)',
 '12. THE SEARCHERS (1956)',
 '13. STAR WARS (1977)',
 '14. PSYCHO (1960)',
 '15. 2001: A SPACE ODYSSEY (1968)',
 '16. SUNSET BLVD. (1950)',
 '17. THE GRADUATE (1967)',
 '18. THE GENERAL (1927)',
 '19. ON THE WATERFRONT (1954)',
 "20. IT'S A WONDERFUL LIFE (1947)",
 '21. CHINATOWN (1974)',
 '22. SOME LIKE IT HOT (1959)',
 '23. THE GRAPES OF WRATH (1940)',
 '24. E.T.:  THE EXTRA-TERRESTRIAL (1982)',
 '25. TO KILL A MOCKINGBIRD (1962)',
 '26. MR. SMITH GOES TO WASHINGTON (1939)',
 '27. HIGH NOON (1952)',
 '28. ALL ABOUT EVE (1950)',
 '29. DOUBLE INDEMNITY (1944)',
 '30. APOCALYPSE NOW (1979)',
 '31. THE MALTESE FALCON (1941)',
 '32. THE GODFATHER PART II (1974)',
 "33. ONE FL